# Coursera Capstone Week Three Project #
Initially I will webscrape the data, create the data frame, and then use clustering techniques to complete the assignment. 

Completed by Bill Lovell September 2019

## Step one - get data and clean it ##

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 4.5.11
  latest version: 4.7.12

Please update conda by running

    $ conda update -n base -c defaults conda



## Package Plan ##

  environment location: /home/jupyterlab/conda/envs/python

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    geopy-1.20.0               |             py_0          57 KB  conda-forge
    certifi-2019.9.11          |           py36_0         147 KB  conda-forge
    geographiclib-1.49         |             py_0          32 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         237 KB

The following NEW packages will be INSTALLED:

    geographiclib: 1.49-py_0        conda-forge
    geopy:         1.20.0-py_0      conda-forge

The following pac

In [2]:

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

!conda install -c conda-forge geocoder --yes
import geocoder # import geocoder

!conda install -c conda-forge lxml --yes
!conda install -c conda-forge BeautifulSoup4 --yes

print('Libraries imported.')

Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 4.5.11
  latest version: 4.7.12

Please update conda by running

    $ conda update -n base -c defaults conda



## Package Plan ##

  environment location: /home/jupyterlab/conda/envs/python

  added / updated specs: 
    - geocoder


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    click-7.0                  |             py_0          61 KB  conda-forge
    ratelim-0.1.6              |             py_2           6 KB  conda-forge
    geocoder-1.38.1            |             py_1          53 KB  conda-forge
    future-0.17.1              |        py36_1000         701 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         821 KB

The following NEW packages will be INSTALLED:

    future:   0.17.1-py36_1000 co

pip install lxml
pip install BeautifulSoup4

In [3]:
#Load the required tools to complete the webscaping#
from lxml import html
import pandas as pd
from bs4 import BeautifulSoup

In [35]:
#webscrape directly into the Toronto data frame#
toronto= pd.read_html("https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M")
print(toronto[0])

    Postcode           Borough  \
0        M1A      Not assigned   
1        M2A      Not assigned   
2        M3A        North York   
3        M4A        North York   
4        M5A  Downtown Toronto   
5        M5A  Downtown Toronto   
6        M6A        North York   
7        M6A        North York   
8        M7A      Queen's Park   
9        M8A      Not assigned   
10       M9A         Etobicoke   
11       M1B       Scarborough   
12       M1B       Scarborough   
13       M2B      Not assigned   
14       M3B        North York   
15       M4B         East York   
16       M4B         East York   
17       M5B  Downtown Toronto   
18       M5B  Downtown Toronto   
19       M6B        North York   
20       M7B      Not assigned   
21       M8B      Not assigned   
22       M9B         Etobicoke   
23       M9B         Etobicoke   
24       M9B         Etobicoke   
25       M9B         Etobicoke   
26       M9B         Etobicoke   
27       M1C       Scarborough   
28       M1C  

In [36]:
#create a dataframe and check using head#
tor = pd.concat([pd.DataFrame(toronto[0].values.tolist()), toronto[1]], axis=0)
tor.head()
data = pd.DataFrame(tor)

In [37]:
#cut dataframe down to include all rows, and only three columns#
data=data.iloc[0:287,0:3]

In [38]:
#rename columns#
data.rename(columns={ data.columns[0]: "Postcode" }, inplace = True)
data.rename(columns={ data.columns[1]: "Borough" }, inplace = True)
data.rename(columns={ data.columns[2]: "Neighborhood" }, inplace = True)
data.head()

Postcode           Borough      Neighborhood
0      M1A      Not assigned      Not assigned
1      M2A      Not assigned      Not assigned
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront

In [39]:
#removed not assigneds from Borough#
data = data[data.Borough != 'Not assigned']

In [40]:
#replace not assigneds in Neighborhood with the value from Borough#
data['Neighborhood'] = np.where(data['Neighborhood'] == "Not assigned", data['Borough'], data['Neighborhood'])

In [41]:
#check shape#
data.shape

(211, 3)

## Step Two Add Latitude and Longitude data ##

Initially I tried to run the geocoder loop for all the data - 211 rows - this resulted in a number of errors, and time outs

*this is the code used for the whole data set that didn't work
- initialize your variable to None
lat_lng_coords = None

- loop until you get the coordinates
while(lat_lng_coords is None):
  g = geocoder.google('{}, Toronto, Ontario'.format(data))
  lat_lng_coords = g.latlng

latitude = lat_lng_coords[0]
longitude = lat_lng_coords[1]

#Next I tried to run the loop - but on only 10 rows of the data to see if I could get it to run

In [42]:
#create a dataframe of just 10 rows of data
data2 = data.iloc[0:10,]
data2.shape

(10, 3)

#run the data on just 10 rows
# initialize your variable to None
lat_lng_coords = None

# loop until you get the coordinates
while(lat_lng_coords is None):
  g = geocoder.google('{}, Toronto, Ontario'.format(data2))
  lat_lng_coords = g.latlng

latitude = lat_lng_coords[0]
longitude = lat_lng_coords[1]

data2.head()

#running on a subset of the data still didn't work, next I will try and load from the csv

In [47]:
#load the data and check its shape
data3 = pd.read_csv('http://cocl.us/Geospatial_data')
data3.shape

(103, 3)

In [48]:
data3.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [49]:
#checck the shape is still right, but two new columns#
data.shape

(211, 3)

In [50]:
#rename Postal Code to Postcode to act as the index
data3.rename(columns={ data3.columns[0]: "Postcode" }, inplace = True)

In [51]:
#merge the two data frames using Postcode as the index
df = pd.merge(data, data3, how ='inner', on ='Postcode') 

In [52]:
df.shape

(211, 5)

**This is the Data Frame for the Assessment**

In [167]:
df

Postcode           Borough  \
0        M3A        North York   
1        M4A        North York   
2        M5A  Downtown Toronto   
3        M5A  Downtown Toronto   
4        M6A        North York   
5        M6A        North York   
6        M7A      Queen's Park   
7        M9A         Etobicoke   
8        M1B       Scarborough   
9        M1B       Scarborough   
10       M3B        North York   
11       M4B         East York   
12       M4B         East York   
13       M5B  Downtown Toronto   
14       M5B  Downtown Toronto   
15       M6B        North York   
16       M9B         Etobicoke   
17       M9B         Etobicoke   
18       M9B         Etobicoke   
19       M9B         Etobicoke   
20       M9B         Etobicoke   
21       M1C       Scarborough   
22       M1C       Scarborough   
23       M1C       Scarborough   
24       M3C        North York   
25       M3C        North York   
26       M4C         East York   
27       M5C  Downtown Toronto   
28       M6C              York   
29       M9C         Etobicoke   
30       M9C         Etobicoke   
31       M9C         Etobicoke   
32       M9C         Etobicoke   
33       M1E       Scarborough   
34       M1E       Scarborough   
35       M1E       Scarborough   
36       M4E      East Toronto   
37       M5E  Downtown Toronto   
38       M6E              York   
39       M1G       Scarborough   
40       M4G         East York   
41       M5G  Downtown Toronto   
42       M6G  Downtown Toronto   
43       M1H       Scarborough   
44       M2H        North York   
45       M3H        North York   
46       M3H        North York   
47       M3H        North York   
48       M4H         East York   
49       M5H  Downtown Toronto   
50       M5H  Downtown Toronto   
51       M5H  Downtown Toronto   
52       M6H      West Toronto   
53       M6H      West Toronto   
54       M1J       Scarborough   
55       M2J        North York   
56       M2J        North York   
57       M2J        North York   
58       M3J        North York   
59       M3J        North York   
60       M4J         East York   
61       M5J  Downtown Toronto   
62       M5J  Downtown Toronto   
63       M5J  Downtown Toronto   
64       M6J      West Toronto   
65       M6J      West Toronto   
66       M1K       Scarborough   
67       M1K       Scarborough   
68       M1K       Scarborough   
69       M2K        North York   
70       M3K        North York   
71       M3K        North York   
72       M4K      East Toronto   
73       M4K      East Toronto   
74       M5K  Downtown Toronto   
75       M5K  Downtown Toronto   
76       M6K      West Toronto   
77       M6K      West Toronto   
78       M6K      West Toronto   
79       M1L       Scarborough   
80       M1L       Scarborough   
81       M1L       Scarborough   
82       M2L        North York   
83       M2L        North York   
84       M3L        North York   
85       M4L      East Toronto   
86       M4L      East Toronto   
87       M5L  Downtown Toronto   
88       M5L  Downtown Toronto   
89       M6L        North York   
90       M6L        North York   
91       M6L        North York   
92       M9L        North York   
93       M1M       Scarborough   
94       M1M       Scarborough   
95       M1M       Scarborough   
96       M2M        North York   
97       M2M        North York   
98       M3M        North York   
99       M4M      East Toronto   
100      M5M        North York   
101      M5M        North York   
102      M6M              York   
103      M6M              York   
104      M6M              York   
105      M6M              York   
106      M9M        North York   
107      M9M        North York   
108      M1N       Scarborough   
109      M1N       Scarborough   
110      M2N        North York   
111      M3N        North York   
112      M4N   Central Toronto   
113      M5N   Central Toronto   
114      M6N              York   
115      M6N              York   
116      M9N              

## Step Three Clustering Analysis ##

In [53]:
df.head()

Postcode           Borough      Neighborhood   Latitude  Longitude
0      M3A        North York         Parkwoods  43.753259 -79.329656
1      M4A        North York  Victoria Village  43.725882 -79.315572
2      M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636
3      M5A  Downtown Toronto       Regent Park  43.654260 -79.360636
4      M6A        North York  Lawrence Heights  43.718518 -79.464763

In [55]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(df['Borough'].unique()),
        df.shape[0]
    )
)

The dataframe has 11 boroughs and 211 neighborhoods.


In [56]:
df1 = df
address = 'Toronto, Ontario'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.653963, -79.387207.


In [58]:
# create map of New York using latitude and longitude values
map_Toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, df1 in zip(df1['Latitude'], df1['Longitude'], df1['Borough'], df1['Neighborhood']):
    label = '{}, {}'.format(df1, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_Toronto)  
    
map_Toronto

Next, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.

Define Foursquare Credentials and Version

In [59]:

CLIENT_ID = 'FNS1LWQRG1YX14TDHYFXMI1R0R10STHTJ1YKF1E355BQREKO' # your Foursquare ID
CLIENT_SECRET = 'OLCSB5XKAN2OTHQV3GMFEOQNXKEUUFFQPII4VSCQ4LX30PLP' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: FNS1LWQRG1YX14TDHYFXMI1R0R10STHTJ1YKF1E355BQREKO
CLIENT_SECRET:OLCSB5XKAN2OTHQV3GMFEOQNXKEUUFFQPII4VSCQ4LX30PLP


In [176]:
df.head()

Postcode           Borough      Neighborhood   Latitude  Longitude
0      M3A        North York         Parkwoods  43.753259 -79.329656
1      M4A        North York  Victoria Village  43.725882 -79.315572
2      M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636
3      M5A  Downtown Toronto       Regent Park  43.654260 -79.360636
4      M6A        North York  Lawrence Heights  43.718518 -79.464763

In [177]:
df.dtypes

Postcode         object
Borough          object
Neighborhood     object
Latitude        float64
Longitude       float64
dtype: object

*Filter the data frame down to just those boroughs that contain Toronto - will make it a bit easier to anlayse and run*

Let's explore the first neighborhood in our dataframe.
Get the neighborhood's name.

In [182]:
df.loc[0, 'Neighborhood']

'Parkwoods'

In [183]:
#Get the neighborhood's latitude and longitude values.

neighborhood_latitude = df.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = df.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = df.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Parkwoods are 43.7532586, -79.3296565.


Now, let's get the top 100 venues that are in Marble Hill within a radius of 500 meters.
First, let's create the GET request URL. Name your URL url2.

In [184]:
LIMIT = 100 # limit of number of venues returned by Foursquare API

radius = 2500 # define radius

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL


'https://api.foursquare.com/v2/venues/explore?&client_id=FNS1LWQRG1YX14TDHYFXMI1R0R10STHTJ1YKF1E355BQREKO&client_secret=OLCSB5XKAN2OTHQV3GMFEOQNXKEUUFFQPII4VSCQ4LX30PLP&v=20180605&ll=43.7532586,-79.3296565&radius=2500&limit=100'

In [185]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5d8483d5a87921002c74a294'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Toronto',
  'headerFullLocation': 'Toronto',
  'headerLocationGranularity': 'city',
  'totalResults': 198,
  'suggestedBounds': {'ne': {'lat': 43.77575862250003,
    'lng': -79.29856519924638},
   'sw': {'lat': 43.73075857749998, 'lng': -79.36074780075361}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4b8991cbf964a520814232e3',
       'name': "Allwyn's Bakery",
       'location': {'address': '81 Underhill drive',
        'lat': 43.75984035203157,
        'lng': -79.32471879917513,
        'labeledLatLngs': [{'label': 'display',
          'lat': 43.75984035203157,
   

In [186]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Now we are ready to clean the json and structure it into a pandas dataframe.

In [187]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name                 categories        lat  \
0              Allwyn's Bakery       Caribbean Restaurant  43.759840   
1  Donalda Golf & Country Club                Golf Course  43.752816   
2           Graydon Hall Manor                Event Space  43.763923   
3                   LA Fitness       Gym / Fitness Center  43.747665   
4           Darband Restaurant  Middle Eastern Restaurant  43.755194   

         lng  
0 -79.324719  
1 -79.342741  
2 -79.342961  
3 -79.347077  
4 -79.348498

In [188]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

100 venues were returned by Foursquare.


Now do it for all of Toronto

In [189]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [190]:

Toronto_venues = getNearbyVenues(names=df['Neighborhood'],
                                   latitudes=df['Latitude'],
                                   longitudes=df['Longitude']
                                  )

Parkwoods
Victoria Village
Harbourfront
Regent Park
Lawrence Heights
Lawrence Manor
Queen's Park
Islington Avenue
Rouge
Malvern
Don Mills North
Woodbine Gardens
Parkview Hill
Ryerson
Garden District
Glencairn
Cloverdale
Islington
Martin Grove
Princess Gardens
West Deane Park
Highland Creek
Rouge Hill
Port Union
Flemingdon Park
Don Mills South
Woodbine Heights
St. James Town
Humewood-Cedarvale
Bloordale Gardens
Eringate
Markland Wood
Old Burnhamthorpe
Guildwood
Morningside
West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor
Downsview North
Wilson Heights
Thorncliffe Park
Adelaide
King
Richmond
Dovercourt Village
Dufferin
Scarborough Village
Fairview
Henry Farm
Oriole
Northwood Park
York University
East Toronto
Harbourfront East
Toronto Islands
Union Station
Little Portugal
Trinity
East Birchmount Park
Ionview
Kennedy Park
Bayview Village
CFB Toronto
Downsview East
The Danforth West
Riverdale
Design E

In [192]:
print(Toronto_venues.shape)
Toronto_venues.head()

(4442, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2  Victoria Village              43.725882              -79.315572   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                    Venue  Venue Latitude  Venue Longitude  \
0         Brookbanks Park       43.751976       -79.332140   
1           Variety Store       43.751974       -79.333114   
2  Victoria Village Arena       43.723481       -79.315635   
3             Tim Hortons       43.725517       -79.313103   
4               Portugril       43.725819       -79.312785   

          Venue Category  
0                   Park  
1      Food & Drink Shop  
2           Hockey Arena  
3            Coffee Shop  
4  Portuguese Restaurant

In [193]:
#Let's check how many venues were returned for each neighborhood

Toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                               
Adelaide                                                             100   
Agincourt                                                              5   
Agincourt North                                                        2   
Albion Gardens                                                        11   
Alderwood                                                              9   
Bathurst Manor                                                        18   
Bathurst Quay                                                         16   
Bayview Village                                                        4   
Beaumond Heights                                                      11   
Bedford Park                                                          21   
Berczy Park                                                           56   
Birch Cliff                                                            4   
Bloordale Gardens                                                      9   
Brockton                                                              21   
Business Reply Mail Processing Centre 969 Eastern                     15   
CFB Toronto                                                            2   
CN Tower                                                              16   
Cabbagetown                                                           46   
Caledonia-Fairbanks                                                    5   
Canada Post Gateway Processing Centre                                 11   
Cedarbrae                                                              7   
Central Bay Street                                                    83   
Chinatown                                                            100   
Christie                                                              16   
Church and Wellesley                                                  92   
Clairlea                                                              10   
Clarks Corners                                                        10   
Cliffcrest                                                             3   
Cliffside                                                              3   
Cliffside West                                                         4   
Cloverdale                                                             2   
Commerce Court                                                       100   
Davisville                                                            34   
Davisville North                                                       8   
Deer Park                                                             15   
Del Ray                                                                4   
Design Exchange                                                      100   
Don Mills North                                                        5   
Don Mills South                                                       23   
Dorset Park                                                            6   
Dovercourt Village                                                    15   
Downsview                                                              4   
Downsview Central                                                      3   
Downsview East                                                         2   
Downsview North                                                       18   
Downsview Northwest                                                    4   
Downsview West                                                         6   
Dufferin                                                              15   
East Birchmount Park                                                   6   
East Toronto                                                           3   
Emery                                                                  2   
Eringate               

In [194]:
#Let's find out how many unique categories can be curated from all the returned venues
print('There are {} uniques categories.'.format(len(Toronto_venues['Venue Category'].unique())))

There are 275 uniques categories.


##Analyse each neighborhood##

In [195]:
# one hot encoding
tr_onehot = pd.get_dummies(Toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
tr_onehot['Neighborhood'] = Toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [tr_onehot.columns[-1]] + list(tr_onehot.columns[:-1])
tr_onehot = tr_onehot[fixed_columns]

tr_onehot.head()

Yoga Studio  Accessories Store  Afghan Restaurant  Airport  \
0            0                  0                  0        0   
1            0                  0                  0        0   
2            0                  0                  0        0   
3            0                  0                  0        0   
4            0                  0                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           0                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   Auto Garage  Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0            0              0          0           0           0       0   
1            0              0          0           0           0       0   
2            0              0          0           0           0       0   
3            0              0          0           0           0       0   
4            0              0          0           0           0       0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0     0    0               0                 0                 0   
1     0    0               0                 0                 0   
2     0    0               0                 0                 0   
3     0    0               0                 0                 0   
4     0    0               0                 0                 0   

   Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  Beer Store  \
0                   0      0                0         0           0   
1                   0      0                0         0           0   
2                   0      0                0         0           0   
3                   0      0                0         0           0   
4                   0      0                0         0           0   

   Belgian Restaurant  Bike Shop  Bistro  Boat or Ferry  Bookstore  Boutique  \
0                   0          0       0              0          0         0   
1                   0          0       0              0          0         0   
2                   0          0       0              0          0         0   
3                   0          0       0              0          0         0   
4                   0          0       0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \

In [196]:
#the columns came out in a weird order - so create a new data frame with Neighborhood as the first column
cols = list(tr_onehot.columns.values)
cols

['Yoga Studio',
 'Accessories Store',
 'Afghan Restaurant',
 'Airport',
 'Airport Food Court',
 'Airport Gate',
 'Airport Lounge',
 'Airport Service',
 'Airport Terminal',
 'American Restaurant',
 'Antique Shop',
 'Aquarium',
 'Art Gallery',
 'Art Museum',
 'Arts & Crafts Store',
 'Asian Restaurant',
 'Athletics & Sports',
 'Auto Garage',
 'Auto Workshop',
 'BBQ Joint',
 'Baby Store',
 'Bagel Shop',
 'Bakery',
 'Bank',
 'Bar',
 'Baseball Field',
 'Baseball Stadium',
 'Basketball Court',
 'Basketball Stadium',
 'Beach',
 'Bed & Breakfast',
 'Beer Bar',
 'Beer Store',
 'Belgian Restaurant',
 'Bike Shop',
 'Bistro',
 'Boat or Ferry',
 'Bookstore',
 'Boutique',
 'Brazilian Restaurant',
 'Breakfast Spot',
 'Brewery',
 'Bridal Shop',
 'Bubble Tea Shop',
 'Building',
 'Burger Joint',
 'Burrito Place',
 'Bus Line',
 'Bus Station',
 'Butcher',
 'Café',
 'Cajun / Creole Restaurant',
 'Camera Store',
 'Candy Store',
 'Caribbean Restaurant',
 'Cheese Shop',
 'Chinese Restaurant',
 'Chocolate Shop'

In [197]:
tr_one = tr_onehot[['Neighborhood', 'Yoga Studio',
 'Accessories Store',
 'Afghan Restaurant',
 'Airport',
 'Airport Food Court',
 'Airport Gate',
 'Airport Lounge',
 'Airport Service',
 'Airport Terminal',
 'American Restaurant',
 'Antique Shop',
 'Aquarium',
 'Art Gallery',
 'Art Museum',
 'Arts & Crafts Store',
 'Asian Restaurant',
 'Athletics & Sports',
 'Auto Garage',
 'Auto Workshop',
 'BBQ Joint',
 'Baby Store',
 'Bagel Shop',
 'Bakery',
 'Bank',
 'Bar',
 'Baseball Field',
 'Baseball Stadium',
 'Basketball Court',
 'Basketball Stadium',
 'Beach',
 'Bed & Breakfast',
 'Beer Bar',
 'Beer Store',
 'Belgian Restaurant',
 'Bike Shop',
 'Bistro',
 'Boat or Ferry',
 'Bookstore',
 'Boutique',
 'Brazilian Restaurant',
 'Breakfast Spot',
 'Brewery',
 'Bridal Shop',
 'Bubble Tea Shop',
 'Building',
 'Burger Joint',
 'Burrito Place',
 'Bus Line',
 'Bus Station',
 'Butcher',
 'Café',
 'Cajun / Creole Restaurant',
 'Camera Store',
 'Candy Store',
 'Caribbean Restaurant',
 'Cheese Shop',
 'Chinese Restaurant',
 'Chocolate Shop',
 'Church',
 'Climbing Gym',
 'Clothing Store',
 'Cocktail Bar',
 'Coffee Shop',
 'College Arts Building',
 'College Auditorium',
 'College Gym',
 'College Rec Center',
 'College Stadium',
 'Colombian Restaurant',
 'Comfort Food Restaurant',
 'Comic Shop',
 'Concert Hall',
 'Construction & Landscaping',
 'Convenience Store',
 'Cosmetics Shop',
 'Coworking Space',
 'Creperie',
 'Cuban Restaurant',
 'Cupcake Shop',
 'Curling Ice',
 'Dance Studio',
 'Deli / Bodega',
 'Department Store',
 'Dessert Shop',
 'Dim Sum Restaurant',
 'Diner',
 'Discount Store',
 'Dog Run',
 'Doner Restaurant',
 'Donut Shop',
 'Drugstore',
 'Dumpling Restaurant',
 'Eastern European Restaurant',
 'Electronics Store',
 'Empanada Restaurant',
 'Ethiopian Restaurant',
 'Event Space',
 'Falafel Restaurant',
 'Farmers Market',
 'Fast Food Restaurant',
 'Festival',
 'Field',
 'Filipino Restaurant',
 'Fish & Chips Shop',
 'Fish Market',
 'Flea Market',
 'Flower Shop',
 'Food',
 'Food & Drink Shop',
 'Food Court',
 'Food Truck',
 'Fountain',
 'French Restaurant',
 'Fried Chicken Joint',
 'Frozen Yogurt Shop',
 'Fruit & Vegetable Store',
 'Furniture / Home Store',
 'Gaming Cafe',
 'Garden',
 'Garden Center',
 'Gastropub',
 'Gay Bar',
 'General Entertainment',
 'General Travel',
 'Gift Shop',
 'Gluten-free Restaurant',
 'Golf Course',
 'Gourmet Shop',
 'Greek Restaurant',
 'Grocery Store',
 'Gym',
 'Gym / Fitness Center',
 'Hakka Restaurant',
 'Harbor / Marina',
 'Hardware Store',
 'Health & Beauty Service',
 'Health Food Store',
 'Historic Site',
 'History Museum',
 'Hobby Shop',
 'Hockey Arena',
 'Home Service',
 'Hookah Bar',
 'Hospital',
 'Hostel',
 'Hotel',
 'Hotel Bar',
 'Hotpot Restaurant',
 'Ice Cream Shop',
 'Indian Restaurant',
 'Indie Movie Theater',
 'Indonesian Restaurant',
 'Indoor Play Area',
 'Intersection',
 'Irish Pub',
 'Italian Restaurant',
 'Japanese Restaurant',
 'Jazz Club',
 'Jewelry Store',
 'Jewish Restaurant',
 'Juice Bar',
 'Korean Restaurant',
 'Lake',
 'Latin American Restaurant',
 'Light Rail Station',
 'Lingerie Store',
 'Liquor Store',
 'Lounge',
 'Mac & Cheese Joint',
 'Malay Restaurant',
 'Market',
 'Martial Arts Dojo',
 'Massage Studio',
 'Medical Center',
 'Mediterranean Restaurant',
 "Men's Store",
 'Metro Station',
 'Mexican Restaurant',
 'Middle Eastern Restaurant',
 'Miscellaneous Shop',
 'Mobile Phone Shop',
 'Modern European Restaurant',
 'Molecular Gastronomy Restaurant',
 'Monument / Landmark',
 'Motel',
 'Movie Theater',
 'Moving Target',
 'Museum',
 'Music Venue',
 'New American Restaurant',
 'Nightclub',
 'Noodle House',
 'Office',
 'Opera House',
 'Optical Shop',
 'Organic Grocery',
 'Other Great Outdoors',
 'Park',
 'Performing Arts Venue',
 'Persian Restaurant',
 'Pet Store',
 'Pharmacy',
 'Pizza Place',
 'Plane',
 'Playground',
 'Plaza',
 'Poke Place',
 'Polish Restaurant',
 'Pool',
 'Portuguese Restaurant',
 'Poutine Place',
 'Print Shop',
 'Pub',
 'Ramen Restaurant',
 'Record Shop',
 'Rental Car Location',
 'Restaurant',
 'River',
 'Roof Deck',
 'Sake Bar',
 'Salad Place',
 'Salon / Barbershop',
 'Sandwich Place',
 'Scenic Lookout',
 'Sculpture Garden',
 'Seafood Restaurant',
 'Shoe Repair',
 'Shoe Store',
 'Shopping Mall',
 'Shopping Plaza',
 'Skate Park',
 'Skating Rink',
 'Smoke Shop',
 'Smoothie Shop',
 'Snack Place',
 'Soccer Field',
 'Soup Place',
 'Southern / Soul Food Restaurant',
 'Spa',
 'Speakeasy',
 'Sporting Goods Shop',
 'Sports Bar',
 'Stadium',
 'Stationery Store',
 'Steakhouse',
 'Strip Club',
 'Supermarket',
 'Supplement Shop',
 'Sushi Restaurant',
 'Swim School',
 'Taco Place',
 'Tailor Shop',
 'Taiwanese Restaurant',
 'Tanning Salon',
 'Tapas Restaurant',
 'Tea Room',
 'Tennis Court',
 'Thai Restaurant',
 'Theater',
 'Theme Restaurant',
 'Thrift / Vintage Store',
 'Toy / Game Store',
 'Trail',
 'Train Station',
 'Turkish Restaurant',
 'Vegetarian / Vegan Restaurant',
 'Video Game Store',
 'Video Store',
 'Vietnamese Restaurant',
 'Warehouse Store',
 'Wine Bar',
 'Wine Shop',
 'Wings Joint',
 "Women's Store"]]

In [198]:
tr_one.head()

Neighborhood  Yoga Studio  Accessories Store  Afghan Restaurant  \
0         Parkwoods            0                  0                  0   
1         Parkwoods            0                  0                  0   
2  Victoria Village            0                  0                  0   
3  Victoria Village            0                  0                  0   
4  Victoria Village            0                  0                  0   

   Airport  Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0        0                   0             0               0                0   
1        0                   0             0               0                0   
2        0                   0             0               0                0   
3        0                   0             0               0                0   
4        0                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           0                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   Auto Garage  Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0            0              0          0           0           0       0   
1            0              0          0           0           0       0   
2            0              0          0           0           0       0   
3            0              0          0           0           0       0   
4            0              0          0           0           0       0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0     0    0               0                 0                 0   
1     0    0               0                 0                 0   
2     0    0               0                 0                 0   
3     0    0               0                 0                 0   
4     0    0               0                 0                 0   

   Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  Beer Store  \
0                   0      0                0         0           0   
1                   0      0                0         0           0   
2                   0      0                0         0           0   
3                   0      0                0         0           0   
4                   0      0                0         0           0   

   Belgian Restaurant  Bike Shop  Bistro  Boat or Ferry  Bookstore  Boutique  \
0                   0          0       0              0          0         0   
1                   0          0       0              0          0         0   
2                   0          0       0              0          0         0   
3                   0          0       0              0          0         0   
4                   0          0       0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0         

In [199]:
tr_one.shape

(4442, 275)

In [200]:
#Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category
tr_grouped = tr_one.groupby('Neighborhood').mean().reset_index()
tr_grouped

Neighborhood  Yoga Studio  \
0                                             Adelaide     0.000000   
1                                            Agincourt     0.000000   
2                                      Agincourt North     0.000000   
3                                       Albion Gardens     0.000000   
4                                            Alderwood     0.000000   
5                                       Bathurst Manor     0.000000   
6                                        Bathurst Quay     0.000000   
7                                      Bayview Village     0.000000   
8                                     Beaumond Heights     0.000000   
9                                         Bedford Park     0.000000   
10                                         Berczy Park     0.000000   
11                                         Birch Cliff     0.000000   
12                                   Bloordale Gardens     0.000000   
13                                            Brockton     0.000000   
14   Business Reply Mail Processing Centre 969 Eastern     0.000000   
15                                         CFB Toronto     0.000000   
16                                            CN Tower     0.000000   
17                                         Cabbagetown     0.000000   
18                                 Caledonia-Fairbanks     0.000000   
19               Canada Post Gateway Processing Centre     0.000000   
20                                           Cedarbrae     0.000000   
21                                  Central Bay Street     0.012048   
22                                           Chinatown     0.000000   
23                                            Christie     0.000000   
24                                Church and Wellesley     0.010870   
25                                            Clairlea     0.000000   
26                                      Clarks Corners     0.000000   
27                                          Cliffcrest     0.000000   
28                                           Cliffside     0.000000   
29                                      Cliffside West     0.000000   
30                                          Cloverdale     0.000000   
31                                      Commerce Court     0.000000   
32                                          Davisville     0.000000   
33                                    Davisville North     0.000000   
34                                           Deer Park     0.000000   
35                                             Del Ray     0.000000   
36                                     Design Exchange     0.000000   
37                                     Don Mills North     0.000000   
38                                     Don Mills South     0.000000   
39                                         Dorset Park     0.000000   
40                                  Dovercourt Village     0.000000   
41                                           Downsview     0.000000   
42                                   Downsview Central     0.000000   
43                                      Downsview East     0.000000   
44                                     Downsview North     0.000000   
45                                 Downsview Northwest     0.000000   
46                                      Downsview West     0.000000   
47                                            Dufferin     0.000000   
48                                East Birchmount Park     0.000000   
49                                        East Toronto     0.000000   
50                                               Emery     0.000000   
51                                            Eringate     0.000000   
52                                    Exhibition Place     0.000000   
53                                            Fairview     0.000000   
54                                First Canadian Place     0.000000   
55                                     Flemingdon Park     0.00000

In [201]:
#Let's print each neighborhood along with the top 5 most common venues

num_top_venues = 5

for hood in tr_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = tr_grouped[tr_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide----
         venue  freq
0  Coffee Shop  0.08
1         Café  0.05
2          Bar  0.04
3   Steakhouse  0.04
4   Restaurant  0.03


----Agincourt----
                venue  freq
0      Sandwich Place   0.2
1      Breakfast Spot   0.2
2  Chinese Restaurant   0.2
3              Lounge   0.2
4        Skating Rink   0.2


----Agincourt North----
                      venue  freq
0                Playground   0.5
1                      Park   0.5
2            Medical Center   0.0
3  Mediterranean Restaurant   0.0
4               Men's Store   0.0


----Albion Gardens----
                 venue  freq
0        Grocery Store  0.18
1  Fried Chicken Joint  0.09
2          Pizza Place  0.09
3             Pharmacy  0.09
4       Sandwich Place  0.09


----Alderwood----
          venue  freq
0   Pizza Place  0.22
1   Coffee Shop  0.11
2           Gym  0.11
3  Skating Rink  0.11
4  Dance Studio  0.11


----Bathurst Manor----
                       venue  freq
0                Coffee Shop

In [271]:
#put all that in a DF - sort by popularity

def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [272]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = tr_grouped['Neighborhood']

for ind in np.arange(tr_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(tr_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head(15)

Neighborhood 1st Most Common Venue  \
0                                            Adelaide           Coffee Shop   
1                                           Agincourt        Sandwich Place   
2                                     Agincourt North            Playground   
3                                      Albion Gardens         Grocery Store   
4                                           Alderwood           Pizza Place   
5                                      Bathurst Manor           Coffee Shop   
6                                       Bathurst Quay       Airport Service   
7                                     Bayview Village   Japanese Restaurant   
8                                    Beaumond Heights         Grocery Store   
9                                        Bedford Park    Italian Restaurant   
10                                        Berczy Park           Coffee Shop   
11                                        Birch Cliff       College Stadium   
12                                  Bloordale Gardens              Pharmacy   
13                                           Brockton           Coffee Shop   
14  Business Reply Mail Processing Centre 969 Eastern        Farmers Market   

   2nd Most Common Venue        3rd Most Common Venue  4th Most Common Venue  \
0                   Café                          Bar             Steakhouse   
1                 Lounge               Breakfast Spot           Skating Rink   
2                   Park  Eastern European Restaurant         Discount Store   
3               Pharmacy          Fried Chicken Joint            Pizza Place   
4            Coffee Shop                 Skating Rink         Sandwich Place   
5          Deli / Bodega               Sandwich Place             Restaurant   
6       Airport Terminal               Airport Lounge          Boat or Ferry   
7                   Café           Chinese Restaurant                   Bank   
8               Pharmacy          Fried Chicken Joint            Pizza Place   
9            Coffee Shop                  Pizza Place       Sushi Restaurant   
10          Cocktail Bar           Seafood Restaurant                   Café   
11          Skating Rink        General Entertainment                   Café   
12           Pizza Place                    Pet Store                   Park   
13        Breakfast Spot                         Café  Performing Arts Venue   
14         Garden Center                   Skate Park   Fast Food Restaurant   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0         Cosmetics Shop       Thai Restaurant                 Hotel   
1     Chinese Restaurant   Dumpling Restaurant               Dog Run   
2                Dog Run      Doner Restaurant            Donut Shop   
3             Beer Store        Discount Store        Sandwich Place   
4                    Pub          Dance Studio              Pharmacy   
5                   Bank           Supermarket   Fried Chicken Joint   
6            Coffee Shop      Sculpture Garden                 Plane   
7                Dog Run      Doner Restaurant            Donut Shop   
8             Beer Store        Discount Store        Sandwich Place   
9       Greek Restaurant     Indian Restaurant             Juice Bar   
10        Farmers Market            Steakhouse              Beer Bar   
11  Ethiopian Restaurant   Empanada Restaurant           Event Space   
12          Liquor Store            Beer Store           Coffee Shop   
13            Restaurant                   Bar                Bakery   
14                   Spa               Brewery    Light Rail Station   

   8th Most Common Venue        9th Most Common Venue  \
0             Restaurant                 Burger Joint   
1       Doner Restaurant                   Donut Shop   
2              Drugstore          Dumpling Restaurant   
3    Japanese Restaurant         Fast Food Restaurant   
4                    Gym         Ethiopian Restaurant   


## Cluster the neighborhoods ##

In [273]:
# set number of clusters
kclusters = 5

tr_grouped_clustering1 = tr_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(tr_grouped_clustering1)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 4, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

In [274]:
#Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

tr_merged = df

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
tr_merged = tr_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

tr_merged.head(15) # check the last columns!


Postcode           Borough      Neighborhood   Latitude  Longitude  \
0       M3A        North York         Parkwoods  43.753259 -79.329656   
1       M4A        North York  Victoria Village  43.725882 -79.315572   
2       M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636   
3       M5A  Downtown Toronto       Regent Park  43.654260 -79.360636   
4       M6A        North York  Lawrence Heights  43.718518 -79.464763   
5       M6A        North York    Lawrence Manor  43.718518 -79.464763   
6       M7A      Queen's Park      Queen's Park  43.662301 -79.389494   
7       M9A         Etobicoke  Islington Avenue  43.667856 -79.532242   
8       M1B       Scarborough             Rouge  43.806686 -79.194353   
9       M1B       Scarborough           Malvern  43.806686 -79.194353   
10      M3B        North York   Don Mills North  43.745906 -79.352188   
11      M4B         East York  Woodbine Gardens  43.706397 -79.309937   
12      M4B         East York     Parkview Hill  43.706397 -79.309937   
13      M5B  Downtown Toronto           Ryerson  43.657162 -79.378937   
14      M5B  Downtown Toronto   Garden District  43.657162 -79.378937   

    Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0              3.0     Food & Drink Shop                  Park   
1              0.0          Intersection          Hockey Arena   
2              0.0           Coffee Shop                   Pub   
3              0.0           Coffee Shop                   Pub   
4              0.0        Clothing Store         Women's Store   
5              0.0        Clothing Store         Women's Store   
6              0.0           Coffee Shop                  Park   
7              NaN                   NaN                   NaN   
8              0.0  Fast Food Restaurant            Print Shop   
9              0.0  Fast Food Restaurant            Print Shop   
10             0.0   Japanese Restaurant                  Café   
11             0.0           Pizza Place  Fast Food Restaurant   
12             0.0           Pizza Place  Fast Food Restaurant   
13             0.0           Coffee Shop        Clothing Store   
14             0.0           Coffee Shop        Clothing Store   

          3rd Most Common Venue 4th Most Common Venue  \
0             Electronics Store               Dog Run   
1         Portuguese Restaurant           Coffee Shop   
2                        Bakery                  Park   
3                        Bakery                  Park   
4        Furniture / Home Store    Miscellaneous Shop   
5        Furniture / Home Store    Miscellaneous Shop   
6                           Gym                 Diner   
7                           NaN                   NaN   
8   Eastern European Restaurant        Discount Store   
9   Eastern European Restaurant        Discount Store   
10         Caribbean Restaurant  Gym / Fitness Center   
11                     Pharmacy             Gastropub   
12                     Pharmacy             Gastropub   
13    Middle Eastern Restaurant        Cosmetics Shop   
14    Middle Eastern Restaurant        Cosmetics Shop   

          5th Most Common Venue 6th Most Common Venue  7th Most Common Venue  \
0              Doner Restaurant            Donut Shop              Drugstore   
1   Eastern European Restaurant        Discount Store                Dog Run   
2                          Café    Mexican Restaurant                Theater   
3                          Café    Mexican Restaurant                Theater   
4             Accessories Store              Boutique  Vietnamese Restaurant   
5             Accessories Store              Boutique  Vietnamese Restaurant   
6                   Yoga Studio    Seafood Restaurant           Burger Joint   
7                           NaN                   NaN                    NaN   
8                       Dog Run      Doner Restaurant             Donut Shop   
9                       Dog Run      Doner Restaurant           

In [275]:
#there are Nan in the Clusters - drop them using Cluster Labels as a proxy
tr_merged = tr_merged.dropna(subset=['Cluster Labels'])

In [276]:
tr_merged.head()

Postcode           Borough      Neighborhood   Latitude  Longitude  \
0      M3A        North York         Parkwoods  43.753259 -79.329656   
1      M4A        North York  Victoria Village  43.725882 -79.315572   
2      M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636   
3      M5A  Downtown Toronto       Regent Park  43.654260 -79.360636   
4      M6A        North York  Lawrence Heights  43.718518 -79.464763   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0             3.0     Food & Drink Shop                  Park   
1             0.0          Intersection          Hockey Arena   
2             0.0           Coffee Shop                   Pub   
3             0.0           Coffee Shop                   Pub   
4             0.0        Clothing Store         Women's Store   

    3rd Most Common Venue 4th Most Common Venue        5th Most Common Venue  \
0       Electronics Store               Dog Run             Doner Restaurant   
1   Portuguese Restaurant           Coffee Shop  Eastern European Restaurant   
2                  Bakery                  Park                         Café   
3                  Bakery                  Park                         Café   
4  Furniture / Home Store    Miscellaneous Shop            Accessories Store   

  6th Most Common Venue  7th Most Common Venue 8th Most Common Venue  \
0            Donut Shop              Drugstore   Dumpling Restaurant   
1        Discount Store                Dog Run      Doner Restaurant   
2    Mexican Restaurant                Theater  Gym / Fitness Center   
3    Mexican Restaurant                Theater  Gym / Fitness Center   
4              Boutique  Vietnamese Restaurant           Coffee Shop   

         9th Most Common Venue 10th Most Common Venue  
0  Eastern European Restaurant          Women's Store  
1                   Donut Shop              Drugstore  
2               Breakfast Spot          Historic Site  
3               Breakfast Spot          Historic Site  
4                    Gift Shop                Dog Run

In [279]:
#Explore the clusters using a map
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(tr_merged['Latitude'], tr_merged['Longitude'], tr_merged['Neighborhood'], tr_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=7,
        popup= label,
        color=rainbow[int(cluster)],
        fill=True,
        fill_color=rainbow[int(cluster)],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

Examine the clusters

Cluster 1

In [280]:
tr_merged.loc[tr_merged['Cluster Labels'] == 0, tr_merged.columns[[1] + list(range(5, tr_merged.shape[1]))]]

Borough  Cluster Labels      1st Most Common Venue  \
1          North York             0.0               Intersection   
2    Downtown Toronto             0.0                Coffee Shop   
3    Downtown Toronto             0.0                Coffee Shop   
4          North York             0.0             Clothing Store   
5          North York             0.0             Clothing Store   
6        Queen's Park             0.0                Coffee Shop   
8         Scarborough             0.0       Fast Food Restaurant   
9         Scarborough             0.0       Fast Food Restaurant   
10         North York             0.0        Japanese Restaurant   
11          East York             0.0                Pizza Place   
12          East York             0.0                Pizza Place   
13   Downtown Toronto             0.0                Coffee Shop   
14   Downtown Toronto             0.0                Coffee Shop   
15         North York             0.0                Pizza Place   
16          Etobicoke             0.0                  Gift Shop   
17          Etobicoke             0.0                  Gift Shop   
18          Etobicoke             0.0                  Gift Shop   
19          Etobicoke             0.0                  Gift Shop   
20          Etobicoke             0.0                  Gift Shop   
24         North York             0.0           Asian Restaurant   
25         North York             0.0           Asian Restaurant   
26          East York             0.0               Skating Rink   
27   Downtown Toronto             0.0                Coffee Shop   
28               York             0.0                     Garden   
29          Etobicoke             0.0                   Pharmacy   
30          Etobicoke             0.0                   Pharmacy   
31          Etobicoke             0.0                   Pharmacy   
32          Etobicoke             0.0                   Pharmacy   
33        Scarborough             0.0                Pizza Place   
34        Scarborough             0.0                Pizza Place   
35        Scarborough             0.0                Pizza Place   
36       East Toronto             0.0          Health Food Store   
37   Downtown Toronto             0.0                Coffee Shop   
39        Scarborough             0.0                Coffee Shop   
40          East York             0.0                Coffee Shop   
41   Downtown Toronto             0.0                Coffee Shop   
42   Downtown Toronto             0.0              Grocery Store   
43        Scarborough             0.0           Hakka Restaurant   
44         North York             0.0       Fast Food Restaurant   
45         North York             0.0                Coffee Shop   
46         North York             0.0                Coffee Shop   
47         North York             0.0                Coffee Shop   
48          East York             0.0          Indian Restaurant   
49   Downtown Toronto             0.0                Coffee Shop   
50   Downtown Toronto             0.0                Coffee Shop   
51   Downtown Toronto             0.0                Coffee Shop   
52       West Toronto             0.0                     Bakery   
53       West Toronto             0.0                     Bakery   
55         North York             0.0             Clothing Store   
56         North York             0.0             Clothing Store   
57         North York             0.0             Clothing Store   
58         North York             0.0             Massage Studio   
59         North York             0.0             Massage Studio   
61   Downtown Toronto             0.0                Coffee Shop   
62   Downtown Toronto             0.0                Coffee Shop   
63   Downtown Toronto             0.0                Coffee Shop   
64       West Toronto             0.0                        Bar   
65       West Toronto             0.0                        Bar   
66

Cluster 2

In [282]:
tr_merged.loc[tr_merged['Cluster Labels'] == 1, tr_merged.columns[[1] + list(range(5, tr_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
21  Scarborough             1.0                   Bar         Women's Store   
22  Scarborough             1.0                   Bar         Women's Store   
23  Scarborough             1.0                   Bar         Women's Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
21     Electronics Store      Doner Restaurant            Donut Shop   
22     Electronics Store      Doner Restaurant            Donut Shop   
23     Electronics Store      Doner Restaurant            Donut Shop   

   6th Most Common Venue 7th Most Common Venue        8th Most Common Venue  \
21             Drugstore   Dumpling Restaurant  Eastern European Restaurant   
22             Drugstore   Dumpling Restaurant  Eastern European Restaurant   
23             Drugstore   Dumpling Restaurant  Eastern European Restaurant   

   9th Most Common Venue 10th Most Common Venue  
21   Empanada Restaurant         Discount Store  
22   Empanada Restaurant         Discount Store  
23   Empanada Restaurant         Discount Store

Cluster 3

In [283]:
tr_merged.loc[tr_merged['Cluster Labels'] == 2, tr_merged.columns[[1] + list(range(5, tr_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue   2nd Most Common Venue  \
106  North York             2.0        Baseball Field  Furniture / Home Store   
107  North York             2.0        Baseball Field  Furniture / Home Store   
198   Etobicoke             2.0        Baseball Field                    Pool   
199   Etobicoke             2.0        Baseball Field                    Pool   
200   Etobicoke             2.0        Baseball Field                    Pool   
201   Etobicoke             2.0        Baseball Field                    Pool   
202   Etobicoke             2.0        Baseball Field                    Pool   
203   Etobicoke             2.0        Baseball Field                    Pool   
204   Etobicoke             2.0        Baseball Field                    Pool   
205   Etobicoke             2.0        Baseball Field                    Pool   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
106         Women's Store      Doner Restaurant            Donut Shop   
107         Women's Store      Doner Restaurant            Donut Shop   
198         Women's Store               Dog Run      Doner Restaurant   
199         Women's Store               Dog Run      Doner Restaurant   
200         Women's Store               Dog Run      Doner Restaurant   
201         Women's Store               Dog Run      Doner Restaurant   
202         Women's Store               Dog Run      Doner Restaurant   
203         Women's Store               Dog Run      Doner Restaurant   
204         Women's Store               Dog Run      Doner Restaurant   
205         Women's Store               Dog Run      Doner Restaurant   

    6th Most Common Venue 7th Most Common Venue        8th Most Common Venue  \
106             Drugstore   Dumpling Restaurant  Eastern European Restaurant   
107             Drugstore   Dumpling Restaurant  Eastern European Restaurant   
198            Donut Shop             Drugstore          Dumpling Restaurant   
199            Donut Shop             Drugstore          Dumpling Restaurant   
200            Donut Shop             Drugstore          Dumpling Restaurant   
201            Donut Shop             Drugstore          Dumpling Restaurant   
202            Donut Shop             Drugstore          Dumpling Restaurant   
203            Donut Shop             Drugstore          Dumpling Restaurant   
204            Donut Shop             Drugstore          Dumpling Restaurant   
205            Donut Shop             Drugstore          Dumpling Restaurant   

           9th Most Common Venue 10th Most Common Venue  
106            Electronics Store         Discount Store  
107            Electronics Store         Discount Store  
198  Eastern European Restaurant      Electronics Store  
199  Eastern European Restaurant      Electronics Store  
200  Eastern European Restaurant      Electronics Store  
201  Eastern European Restaurant      Electronics Store  
202  Eastern European Restaurant      Electronics Store  
203  Eastern European Restaurant      Electronics Store  
204  Eastern European Restaurant      Electronics Store  
205  Eastern European Restaurant      Electronics Store

Cluster 4

In [284]:
tr_merged.loc[tr_merged['Cluster Labels'] == 3, tr_merged.columns[[1] + list(range(5, tr_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
0         North York             3.0     Food & Drink Shop   
38              York             3.0                  Park   
60         East York             3.0     Convenience Store   
70        North York             3.0               Airport   
71        North York             3.0               Airport   
89        North York             3.0      Basketball Court   
90        North York             3.0      Basketball Court   
91        North York             3.0      Basketball Court   
112  Central Toronto             3.0              Bus Line   
116             York             3.0                  Park   
120       North York             3.0     Convenience Store   
137        Etobicoke             3.0           Pizza Place   
138        Etobicoke             3.0           Pizza Place   
139        Etobicoke             3.0           Pizza Place   
140        Etobicoke             3.0           Pizza Place   
150  Central Toronto             3.0          Tennis Court   
151  Central Toronto             3.0          Tennis Court   
193        Etobicoke             3.0                  Pool   
194        Etobicoke             3.0                  Pool   
195        Etobicoke             3.0                  Pool   

          2nd Most Common Venue        3rd Most Common Venue  \
0                          Park            Electronics Store   
38                Women's Store                       Market   
60                  Coffee Shop                         Park   
70                         Park                Women's Store   
71                         Park                Women's Store   
89   Construction & Landscaping                       Bakery   
90   Construction & Landscaping                       Bakery   
91   Construction & Landscaping                       Bakery   
112                        Park                  Swim School   
116           Convenience Store                Women's Store   
120                        Park                         Bank   
137                    Bus Line                         Park   
138                    Bus Line                         Park   
139                    Bus Line                         Park   
140                    Bus Line                         Park   
150                        Park  Eastern European Restaurant   
151                        Park  Eastern European Restaurant   
193                       River                         Park   
194                       River                         Park   
195                       River                         Park   

    4th Most Common Venue        5th Most Common Venue 6th Most Common Venue  \
0                 Dog Run             Doner Restaurant            Donut Shop   
38   Fast Food Restaurant               Farmers Market    Falafel Restaurant   
60          Women's Store  Eastern European Restaurant               Dog Run   
70      Electronics Store                      Dog Run      Doner Restaurant   
71      Electronics Store                      Dog Run      Doner Restaurant   
89                   Park          Empanada Restaurant            Donut Shop   
90                   Park          Empanada Restaurant            Donut Shop   
91                   Park          Empanada Restaurant            Donut Shop   
112         Women's Store          Dumpling Restaurant               Dog Run   
116     Electronics Store                      Dog Run      Doner Restaurant   
120                   Bar                Women's Store     Electronics Store   
137     Mobile Phone Shop          Dumpling Restaurant               Dog Run   
138     Mobile Phone Shop          Dumpling Restaurant               Dog Run   
139     Mobile Phone Shop          Dumpling Restaurant               Dog Run   
140     Mobile Phone Shop          Dumpling Restaurant               Dog Run   
150        Discount Store                      Dog Run      Doner Restaurant   
151  

Cluster 5

In [285]:
tr_merged.loc[tr_merged['Cluster Labels'] == 4, tr_merged.columns[[1] + list(range(5, tr_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
54        Scarborough             4.0            Playground   
155       Scarborough             4.0            Playground   
156       Scarborough             4.0            Playground   
157       Scarborough             4.0            Playground   
158       Scarborough             4.0            Playground   
183  Downtown Toronto             4.0                  Park   

    2nd Most Common Venue        3rd Most Common Venue 4th Most Common Venue  \
54      Convenience Store  Eastern European Restaurant        Discount Store   
155                  Park  Eastern European Restaurant        Discount Store   
156                  Park  Eastern European Restaurant        Discount Store   
157                  Park  Eastern European Restaurant        Discount Store   
158                  Park  Eastern European Restaurant        Discount Store   
183            Playground                     Building                 Trail   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
54                Dog Run      Doner Restaurant            Donut Shop   
155               Dog Run      Doner Restaurant            Donut Shop   
156               Dog Run      Doner Restaurant            Donut Shop   
157               Dog Run      Doner Restaurant            Donut Shop   
158               Dog Run      Doner Restaurant            Donut Shop   
183             Drugstore        Discount Store               Dog Run   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
54              Drugstore   Dumpling Restaurant          Women's Store  
155             Drugstore   Dumpling Restaurant      Electronics Store  
156             Drugstore   Dumpling Restaurant      Electronics Store  
157             Drugstore   Dumpling Restaurant      Electronics Store  
158             Drugstore   Dumpling Restaurant      Electronics Store  
183      Doner Restaurant            Donut Shop    Dumpling Restaurant

Thanky you